<a href="https://colab.research.google.com/github/andrewhinshaw/spotify-song-analysis/blob/main/Interactive_Spotify_Downloader.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Interactive Spotify Downloader

This notebook demonstrates usage of a few Python packages to create a tool for downloading songs from Spotify.

_Let's begin!_

## Contents

- [Getting Started](#scrollTo=yrZeo4yEVhty)
    - [Installing Required Libraries](#scrollTo=niBcZ7DoZvfE)
    - [Installing FFmpeg](#scrollTo=wB0Tp1DvZ8vA)
    - [Importing Libraries](#scrollTo=TLM0iCFSbYUa)
    - [Creating Utility Classes](#scrollTo=0xageS1Hbh6K)
- [Downloading from Spotify](#scrollTo=yLbt_gfpcB49)
    - [Gathering User Input](#scrollTo=R3n4VDSTYov0)
    - [Retrieiving Songs Via Spotdl](#scrollTo=kNuM68BqcSmR)
    - [Selecting Songs to Download](#scrollTo=SNnO3eOIvnic)
    - [Downloading Songs](#scrollTo=Gq082bGdxiFB)
- [Summary](#scrollTo=hzO_xoagh9VE)

---

## Getting Started

Before we get to the fun part, we have a few prerequisities to tackle including installing libraries and dependencies, importing the necessary libraries, and creating utility classes.

### Installing Required Libraries

First, we'll install the required libraries using pip. Using the percent sign before the pip command indicates that we want to install a package rather than execute this as Python code.

In [ ]:
%pip install spotdl

### Installing FFmpeg

Next, we need to download FFmpeg which is required for running spotdl. FFmpeg is an open-sorce library for handling video, audio, and other multimedia.

We can use an exclamation mark to run a shell command inside this notebook to easily download the static ffmpeg build and add it to PATH in this environment.

In [ ]:
# Download a static FFmpeg build and add it to PATH.
exist = !which ffmpeg
if not exist:
    !curl https://johnvansickle.com/ffmpeg/releases/ffmpeg-release-amd64-static.tar.xz -o ffmpeg.tar.xz \
        && tar -xf ffmpeg.tar.xz && rm ffmpeg.tar.xz
    ffmdir = !find . -iname ffmpeg-*-static
    path = %env PATH
    path = path + ':' + ffmdir[0]
    %env PATH $path
install_path = !which ffmpeg
print(f"Successfully install ffmpeg to {install_path[0]}")

Successfully install ffmpeg to /usr/bin/ffmpeg


### Importing Libraries

Next, we'll import all the libraries we'll be using in this notebook. Some notable libraries are:
- `ipywidgets` - Widgets for user input such as dropdowns, text boxes, and buttons
- `google.colab` - Serve downloads to the user from files in the Colab directory

_Note: since spotdl is a command line application, we don't ctually have to import it here._

In [ ]:
import os
import glob

import ipywidgets as widgets
import IPython.display as ipd
from IPython.utils import io
from google.colab import files as gfls

### Creating Utility Classes

This next block creates a basic custom exception which we can raise at any point to gracefully exit a cell's execution. We'll use this later for user input validation.

In [ ]:
class StopExecution(Exception):
    def _render_traceback_(self):
        pass



---



## Downloading from Spotify

The spotdl CLI takes in a Spotify song/album/playlist URL as a parameter, then uses YouTube Music to download and save the file to the local directory. The documentation for spotdl can be found [here](https://github.com/spotDL/spotify-downloader).

Although the documentation and available options for spotdl are very extensive, we'll stick with a very basic implementation for the purpose of this guide. Feel free to make a copy and make your own version as complex as you'd like!

### Gathering User Input

First, we'll use ipywidgets to display a text box where the user can enter a Spotify URL to be downloaded.

In [ ]:
# Create and display the text box for gathering the user's Spotify URL
playlist_url = widgets.Text(
    placeholder="https://open.spotify.com/track/45S5WTQEGOB1VHr1Q4FuPl",
    description="Spotify URL:"
)
display(playlist_url)

Text(value='', description='Spotify URL:', placeholder='https://open.spotify.com/track/45S5WTQEGOB1VHr1Q4FuPl'…

### Retrieving Songs Via Spotdl

If the value entered is blank or not a Spotify URL, we'll raise the custom exception created earlier and display an error message before exiting the cell.

If the user's value is valid, we'll proceed with using spotdl to download the song(s) located at the URL provided. Since spotdl is a command line application, we'll write a basic shell script locally and run that script to start the spotdl download process.

In [ ]:
# Validate user input
if playlist_url.value == "" or "spotify.com" not in playlist_url.value:
    print("Please enter a valid Spotify URL to continue.")
    raise StopExecution

# Create a shell script with the spotdl CLI command
sh = f"spotdl download {playlist_url.value}"
with open("download_script.sh", "w") as file:
    file.write(sh)

print(f"Downloading songs from URL: {playlist_url.value}")

# Wrapping the shell script command with capture_output avoids displaying the
# CLI output which can crash the notebook
with io.capture_output() as captured:
    !bash download_script.sh >> download.log

print("Download complete!")

Download complete!


### Selecting Songs to Download

Next, we'll display a dropdown menu where the user can select one of the songs that was retrieved in the previous step. We'll store this selection in a variable so that the selected song can be served as a download to the user in the next cell.

_Note: any time a new song is downloaded, this cell will need to be re-run to gather all the downloaded songs and display them in the dropdown._

In [ ]:
# Find all the mp3 files in the current directory
files = glob.glob("*.mp3")

# Set the first mp3 file as the actively selected value for the dropdown
selected = None
if len(files) > 0:
    selected = files[0]

# Create and display the dropdown from the available mp3 files
target_file = widgets.Dropdown(
    options=files,
    value=selected,
    description='Select song:',
    disabled=False,
)
display(target_file)

Dropdown(description='Select song:', options=('Harry Styles - Golden.mp3',), value='Harry Styles - Golden.mp3'…

### Previewing the Downloaded Song(s)

Using IPython, we can create a media player to preview the downloaded song that's selected in the dropdown from the previous cell.

_Note: If the dropdow value is changed in the previous cell, this cell will need to be re-run to create the media player for the new value._

In [ ]:
# Create and display media player to preview song
display(ipd.HTML(f"<h3>{target_file.value}</h3>"))
display(ipd.Audio(target_file.value))

### Downloading Songs Locally

Finally, we'll create a button which will trigger the `download` callback function. This function will attempt to serve the file that was selected in the dropdown from the previous cell as a download to be saved on the user's PC.

Try it out!

In [ ]:
# Define a callback function which downloads the file selected in the dropdown
# from the previous cell
def download(event):
    gfls.download(target_file.value)

# Create and display a button which will trigger the download function
button = widgets.Button(
    description="Download",
    disabled=False,
    button_style="",
    tooltip="Download selected file to your PC",
    icon="download"
)
button.on_click(download)
button

Button(description='Download', icon='download', style=ButtonStyle(), tooltip='Download selected file to your P…

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

---

## Summary

Spotify songs can be easily downloaded via the spotdl CLI tool. Since using CLI tools can present friction for non-technical users, the user experience can be improved by building a more interactive interface around the tool. The ipywidgets and IPython libraries provide some useful tools for achieving this through UI elements and widgets for interacting with spotdl.

Ultimately, the UX could be best improved by making it more visual (i.e. through a full-scale web application), but that falls outside the scope of this project 😉